In [ ]:
import torch
import numpy as np
import pandas as pd
import itertools

Load found objects ds

In [ ]:
df = pd.read_csv('assignments_Find+same+or+wimilar+shoes+in+an+online+store_31-01-2020 (6).tsv', sep='\t')
df.head()

In [ ]:
res_df = pd.DataFrame(columns = ['INPUT:image', 'INPUT:left_link', 'INPUT:right_link']) 

for first_index, first_row in df.iterrows():
    for second_index, second_row in df.iterrows():
        if (int(second_index) > int(first_index) and str(first_row['INPUT:image']) == str(second_row['INPUT:image'])):
            new_row = {'INPUT:image': first_row['INPUT:image'],
                    'INPUT:left_link': first_row['OUTPUT:found_link'],
                    'INPUT:right_link': second_row['OUTPUT:found_link']}
            
            res_df = res_df.append(new_row, ignore_index=True)
res_df.to_csv('res_output.tsv', sep='\t', encoding='utf-8', index=False) 
df = pd.read_csv('res_output.tsv', sep='\t')
res_df.head()
   


Load pairwise comparisons

In [ ]:
res = pd.read_csv('assignments_Which+shoes+look+more+similar+than+origin%3F_31-01-2020 (1).tsv', sep='\t')
res['OUTPUT:result'] = res['OUTPUT:result'].apply(lambda x: 1 if x == 'LEFT' else -1)
res['query'] = res['INPUT:image'].apply(lambda x: x + ' ')
res['left_item'] = res[['query','INPUT:left_link']].sum(1)
res['right_item'] = res[['query','INPUT:right_link']].sum(1)

total = len(np.unique(res['ASSIGNMENT:worker_id'].values))
id2ind = dict(zip(np.unique(res['ASSIGNMENT:worker_id'].values), range(total)))
res['ASSIGNMENT:worker_id'] = res['ASSIGNMENT:worker_id'].map(id2ind)

unique_urls = np.unique((*res['left_item'].values, *res['right_item'].values))
total = len(unique_urls)
url2ind = dict(zip(unique_urls, range(total)))
res['left_id'] = res['left_item'].map(url2ind)
res['right_id'] = res['right_item'].map(url2ind)



res.head()

Apply Bradley Terry Model and optimaze parameters using gradient descent

In [ ]:
total_items = len(url2ind)
total_workers = len(id2ind)

s = torch.rand(total_items, requires_grad=True)
q = torch.rand(total_workers, requires_grad=True)
gamma = torch.rand(total_workers, requires_grad=True)

Maximize log likelihood of observed pairwise comparisons

In [ ]:
def count_log_likelihood():

    total = torch.zeros(1)
    sigmoid = torch.nn.Sigmoid()

    for row in res[['left_id', 'right_id', 'OUTPUT:result', 'ASSIGNMENT:worker_id']].iterrows():
        s_i, s_j, y, k = row[1]
        y = torch.Tensor([y])

        total += torch.log(sigmoid(gamma[k]) * sigmoid(y * (s[s_i] - s[s_j])) + (1 - sigmoid(gamma[k])) * sigmoid(y * q[k]))

    return -total

In [ ]:
opt = torch.optim.Adam([s, q, gamma], lr=0.001)

In [ ]:
for iteration in range(100):
    
    opt.zero_grad()
    loss = count_log_likelihood()
    loss.backward()
    opt.step()

    if iteration % 10 == 9:
        print('Iteration: {}, likelihood: {}'.format(iteration + 1, -loss.item()))

Rank found images for each initial image

In [ ]:
for query in set(res['INPUT:image']):
    rows = res[res['INPUT:image'] == query]
    items = list(set(rows['left_item'].values) | set(rows['right_item'].values))
    scores = [s[url2ind[item]].item() for item in items]
    urls = [items[i].split(' ')[1] for i in range(len(items))]
    print("Initial image: ", query)
    for url, score in sorted(zip(urls, scores), key=lambda pair: pair[1] ,reverse = True):
        print(url)
    print('\n\n')

Analysis of workers parameters

In [ ]:
import matplotlib.pyplot as plt

sigmoid = torch.nn.Sigmoid()

fig, axs = plt.subplots(1, 2, figsize=(10, 4))

axs[0].set_title('Left/right bias for random answers')
axs[0].hist(sigmoid(q).detach().numpy(), bins=10, density=True)
axs[0].grid()

axs[1].set_title('Workers reliability')
axs[1].hist(sigmoid(gamma).detach().numpy(), bins=10, density=True)
axs[1].grid()

plt.show()